In [1]:
import numpy as np
from numba import njit
from functools import partial

import pandas as pd
import vectorbt as vbt
import vectorbt as vbt
from vectorbt.utils.colors import adjust_opacity
from vectorbt.utils.enum_ import map_enum_fields
from vectorbt.base.reshape_fns import broadcast, flex_select_auto_nb, to_2d_array
from vectorbt.portfolio.enums import SizeType, Direction, NoOrder, OrderStatus, OrderSide
from vectorbt.portfolio import nb

import talib 

import sys
import os
function_essential_path = r"H:\Desktop\Environement_Trading_Developement\FunctionEssential"
function_s_score_path = r'H:\Desktop\Environement_Trading_Developement\Indicateur'
sys.path.append(function_essential_path)
sys.path.append(function_s_score_path)
import utils as us
import s_score as score
import market_regime as mr

In [2]:
##FONCTION##

def TDI(rsi,fast_period,low_period,midle_period):
    fast_ma = vbt.MA.run(rsi, window=fast_period).ma
    low_ma = vbt.MA.run(rsi, window=low_period).ma
    midle_ma = vbt.MA.run(rsi, window=midle_period).ma
    return fast_ma,low_ma,midle_ma


# calcul l'angle en tout temps entre fast et low 
def angle_fast_low(fast_ma,low_ma,midle_ma,rsi_period):
    fast_shift = fast_ma.shift(1)
    low_shift = low_ma.shift(1)
    angle_fast = np.arctan(fast_ma - fast_shift) * 180 / np.pi
    angle_low = np.arctan(low_ma - low_shift) * 180 / np.pi
    angle = (angle_low + (angle_fast * rsi_period / midle_ma))/(1+rsi_period / midle_ma)
    return angle 

#retourne un pd.Series de la shape de close avec une valeur de bull quand ca croise bull et bear quand ca croise bear et sinon c'est nothing
def cross_fast_low(fast_ma,low_ma):
    fast_shift = fast_ma.shift(1)
    low_shift = low_ma.shift(1)

    cross_bull = ( fast_shift < low_shift ) & (fast_ma > low_ma) 
    cross_bear = ( fast_shift > low_shift ) & (fast_ma < low_ma)

    conditions = [cross_bull,cross_bear]
    choices = ["bull","bear"]
    cross = pd.Series(np.select(conditions,choices,default="nothing"),index=fast_ma.index)

    return cross




In [3]:
def entries_trade(close, sscore, angle, cross, seuil_sscore, force_angle):
    entries_long = [False] * len(close)
    entries_short = [False] * len(close)
    
    for i in range(len(close)):
        if sscore[i] > seuil_sscore:
            for j in range(i+1, min(i+4, len(close))):
                if cross.iloc[j] == "bear" and angle.iloc[j] > force_angle:
                    entries_short[j] = True

        if sscore[i] < -1 * seuil_sscore:
            for j in range(i+1, min(i+4, len(close))):
                if cross.iloc[j] == "bull" and angle.iloc[j] > force_angle:
                    entries_long[j] = True

    return entries_long, entries_short


In [4]:
##INDICATEUR FACTORY##

In [20]:
##CLASS STRATEGIE##

@njit
def pre_sim_func_nb(c):
    entry_price = np.full(c.target_shape[1], np.nan, dtype=np.float64)  
    return (entry_price,)

@njit
def order_func_nb(c, entry_price, long, short, stop_loss, take_profit, size):
    price_now = nb.get_elem_nb(c, c.close)
    entry_long_now = nb.get_elem_nb(c, long)
    entry_short_now = nb.get_elem_nb(c, short)

    if entry_long_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )
        elif c.position_now < 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )  

    if entry_short_now:
        if c.position_now == 0:
            return nb.order_nb(
                size[c.col], 
                price=price_now,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
        elif c.position_now > 0:
            return nb.order_nb(
                -size[c.col],  
                price=price_now,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now > 0:
        SL = entry_price[c.col] * (1 - stop_loss[c.col])
        TP = entry_price[c.col] * (1 + take_profit[c.col])
        
        if price_now >= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.LongOnly,
                fees=0.0005
            )
        elif price_now <= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.LongOnly,
                fees=0.0005
            )

    if c.position_now < 0:
        SL = entry_price[c.col] * (1 + stop_loss[c.col])
        TP = entry_price[c.col] * (1 - take_profit[c.col])
        
        if price_now >= SL:
            return nb.order_nb(
                -size[c.col],
                price=SL,
                direction=Direction.ShortOnly,
                fees=0.0005
            )
        elif price_now <= TP:
            return nb.order_nb(
                -size[c.col],
                price=TP,
                direction=Direction.ShortOnly,
                fees=0.0005
            )

    return NoOrder

@njit
def post_order_func_nb(c, entry_price):
    if c.order_result.status == OrderStatus.Filled:
        entry_price[c.col] = c.order_result.price

class Strategie():

    def __init__(self, data, tickers, frequence_exec, frequence, multitimeframe):
        self.data = data
        self.tickers = tickers
        self.frequence_exec = frequence_exec
        self.frequences = frequence
        self.multitimeframe = multitimeframe  

    def backtest(self, sscore):
        entries_long_df = pd.DataFrame()
        entries_short_df = pd.DataFrame()
        exits_long_df = pd.DataFrame()
        exits_short_df = pd.DataFrame()
        close_df = pd.DataFrame()
        datetime_df = pd.DataFrame()

        for ticker in self.tickers:
            data = self.data[ticker]
            s_score = sscore[ticker]
            close = data['close']
            s_score_ajuster = s_score["adjusted_s_scores_vol"]

            data_reset = data.reset_index()
            datetime = data_reset['Datetime']

            rsi = vbt.RSI.run(close, window=14).rsi
            fast_ma, low_ma, midle_ma = TDI(rsi, 2, 7, 34)
            angle = angle_fast_low(fast_ma, low_ma, midle_ma, 14)
            cross = cross_fast_low(fast_ma, low_ma)

            long, short = entries_trade(close, s_score_ajuster, angle, cross, 1.5, 40)
            long = pd.Series(long, index=data['close'].index)
            short = pd.Series(short, index=data['close'].index)

            # us.print_trades(0,long,short,None,None,data)

            long = long.reset_index(drop=True)
            short = short.reset_index(drop=True)
            close = data['close'].reset_index(drop=True)
            datetime = datetime.reset_index(drop=True)
            entries_long_df[ticker] = long
            entries_short_df[ticker] = short
            close_df[ticker] = close
            datetime_df[ticker] = datetime

        close_df = close_df.replace(0, None).fillna(method='ffill')

        capital = 100000  
        risk_per_trade = 0.01  
        position_value = capital * risk_per_trade  

        size = np.array([position_value / close_df.iloc[-1, i] for i in range(len(self.tickers))])  

        stop_loss = np.array([0.04] * len(self.tickers))  
        take_profit = np.array([0.02] * len(self.tickers))  

        portfolio = vbt.Portfolio.from_order_func(
            close_df,  
            order_func_nb,  
            entries_long_df.values,  
            entries_short_df.values,  
            stop_loss,  
            take_profit,  
            size,  
            freq=self.frequence_exec,  
            init_cash=100000,  # Ajout du capital initial
            pre_sim_func_nb=pre_sim_func_nb,  
            post_order_func_nb=post_order_func_nb,  
            broadcast_named_args=dict(  
                long=entries_long_df.values,  
                short=entries_short_df.values,  
                stop_loss=stop_loss,  
                take_profit=take_profit,  
                size=size  
            )
        )


        us.rapport_backtest(portfolio,close_df,datetime_df,self.tickers)

        return portfolio


In [22]:
##UTILISATION DE LA STRAT##
tickers = ["EURUSD"]
DATA = us.get_data_forex(tickers,'H1',"2000-01-01","2011-01-01")

In [23]:
s_score_value = {}
for ticker in tickers:
    data_traitement = DATA[ticker]
    nb_nan = data_traitement['close'].isna().sum()
    close = data_traitement['close'].dropna()
    close_without_index = close.reset_index()
    result = score.mean_reversion(close, close_without_index['Datetime'], 85, "VOL", 0.5, "EGARCH")
    result_df = pd.DataFrame({
        's_score_value': result[0],
        'adjusted_s_scores_vol': result[1],
        'theta_vals': result[2],
        'mu_vals': result[3],
        'sigma_vals': result[4]
    })
    nan_rows = pd.DataFrame([[float('nan')] * result_df.shape[1]] * nb_nan, columns=result_df.columns)
    result_df = pd.concat([result_df, nan_rows], ignore_index=True)

    s_score_value[ticker] = result_df

Estimation des paramètres OU:   0%|          | 0/51931 [00:00<?, ?it/s]

  0%|          | 0/51931 [00:00<?, ?it/s]

H:\Desktop\Environement_Trading_Developement\Indicateur\s_score.py:31: RuntimeWarning:

invalid value encountered in sqrt

c:\Users\CYTech Student\AppData\Local\Programs\Python\Python311\Lib\site-packages\arch\univariate\base.py:768: ConvergenceWarning:

The optimizer returned code 4. The message is:
Inequality constraints incompatible
See scipy.optimize.fmin_slsqp for code meaning.


Calcul de la volatilité conditionnelle: 100%|██████████| 52016/52016 [00:00<00:00, 444514.68it/s]


52015


C:\Users\CYTech Student\AppData\Local\Temp\ipykernel_17364\4120004593.py:16: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [24]:
strat = Strategie(DATA,tickers,"60m","60m",0)
port = strat.backtest(s_score_value)

C:\Users\CYTech Student\AppData\Local\Temp\ipykernel_17364\3349153716.py:137: FutureWarning:

DataFrame.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.

Estimation des paramètres OU:   0%|          | 0/51931 [00:17<?, ?it/s]



------------------------------------------------------------------DETAILS : EURUSD-----------------------------------------------------------------

Total Return : -0.13%
Benchmark return : 37.67%
CAGR : -0.02%
Volatility : 0.1%
Sharpe Ratio : -0.23
Benchmark sharpe ratio : 0.1
Max Drawdown: -0.35%
Calmar Ratio : -0.06
Beta : 0.0


Total trades : 128
Total long trades 91
Total short trades 37
Win rate : 0.6%
Wining streak : 7.0
Loosing streak : 3.0
Average winning trade : 1.0%
Average losing trade : -2.0%
Profit factor : 0.88
Expectancy : -1.02%



 -> Average duration trades (jour) : 15.1




--------------------------------------------------------------------------------------------------------------------------------------------------

